# 1. Import data

In [1]:
import pandas as pd
import numpy as np
from pyomo.common.timing import report_timing
import pyomo.environ as pyo
from pyomo.environ import *
from pyomo.opt import SolverFactory
from pyomo.opt import SolverStatus, TerminationCondition

In [2]:
data = pd.read_excel('data.xlsx')

In [3]:
data

index NETWORK FLT_TYPE    AREA COUNTRY   ROUTE   SEC2W  \
0     DADHANVN154A3211     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
1     DADHANVN154A3212     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
2     DADHANVN154A3213     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
3     DADHANVN154A3214     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
4     DADHANVN154A3215     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
...                ...     ...      ...     ...     ...     ...     ...   
7868  SYDSGNVN772787C3     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
7869  SYDSGNVN772787C4     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
7870  SYDSGNVN772787C5     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
7871  SYDSGNVN772787C6     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
7872  SYDSGNVN772787C7     INT      PXR     SWP      AU  SGNSYD  SGNSYD   

      Sector from   to flight  DOW_ETD  DOW_ETA        ETD        ETA    AC  \
0     DADHAN  DAD  HAN  VN154        1        2  23.000000   0.333333  A321   
1     DADHAN  DAD  HAN  VN154        2        3  23.000000   0.333333  A321   
2     DADHAN  DAD  HAN  VN154        3        4  23.000000   0.333333  A321   
3     DADHAN  DAD  HAN  VN154        4        5  23.000000   0.333333  A321   
4     DADHAN  DAD  HAN  VN154        5        6  23.000000   0.333333  A321   
...      ...  ...  ...    ...      ...      ...        ...        ...   ...   
7868  SYDSGN  SYD  SGN  VN772        3        3   0.250000   9.166667  787C   
7869  SYDSGN  SYD  SGN  VN772        4        4   0.250000   9.333333  787C   
7870  SYDSGN  SYD  SGN  VN772        5        5   0.250000   9.333333  787C   
7871  SYDSGN  SYD  SGN  VN772        6        6   0.250000   9.333333  787C   
7872  SYDSGN  SYD  SGN  VN772        7        7   2.166667  11.250000  787C   

          revenue         cost  
0      236.346889   201.944430  
1      236.346889   201.944430  
2      236.346889   201.944430  
3      236.346889   201.944430  
4      236.346889   201.944430  
...           ...          ...  
7868  2174.084466  2175.806312  
7869  2174.084466  2175.806312  
7870  2174.084466  2175.806312  
7871  2174.084466  2175.806312  
7872  2174.084466  2175.806312  

[7873 rows x 18 columns]

In [4]:
# tạo dictionary về số tàu bay đã thuê mua:
fleet = {'787A':8,'787B':3,'787C':5,'A350':14,'A321':56}
#fleet = {'AT7':3,'RJ':1}

# 2. Sets

In [5]:
model = pyo.ConcreteModel()

In [6]:
report_timing()

<StreamHandler stdout (NOTSET)>

In [7]:
# create set of sector
model.sector = pyo.Set(initialize = data['Sector'].unique())
sector = model.sector

           0 seconds to construct Set sector; 1 index total


In [8]:
# create set of aircraft type
model.ac_type = pyo.Set(initialize = data['AC'].unique())
ac_type = model.ac_type

           0 seconds to construct Set ac_type; 1 index total


In [9]:
# create set of flight no
model.flight_no = pyo.Set(initialize = data['flight'].unique())
flight_no = model.flight_no

           0 seconds to construct Set flight_no; 1 index total


In [10]:
# create set of DOW
model.DOW = pyo.Set(initialize = range(1,8), domain = PositiveIntegers)
DOW = model.DOW

           0 seconds to construct Set DOW; 1 index total


In [11]:
# create set of hour
model.hour = pyo.Set(initialize = range(0,24), domain = NonNegativeIntegers)
hour = model.hour

           0 seconds to construct Set hour; 1 index total


In [12]:
# create set of airport
airport_from = data['from'].unique()
airport_to = data['to'].unique()
airport_set = set(np.concatenate((airport_from,airport_to)))
model.airport = pyo.Set(initialize = airport_set, ordered = False)
airport = model.airport

           0 seconds to construct Set airport; 1 index total


In [13]:
# Tạo 1 set để làm index các chuyến bay: số hiệu + AC + DOW
model.flight_index = pyo.Set(initialize = data['index'])
flight_index = model.flight_index

    action taken
        0.02 seconds to construct Set flight_index; 1 index total


# 3. Parameters

# 4. Variables

In [14]:
model.assign_fleet = pyo.Var(flight_index, within = Binary, initialize = 1)
assign_fleet = model.assign_fleet

        0.01 seconds to construct Var assign_fleet; 7872 indices total


In [15]:
model.time_nodes = pyo.Var(airport, DOW, hour, ac_type, domain = NonNegativeIntegers)
time_nodes = model.time_nodes

           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
        0.09 seconds to construct Var time_nodes; 52920 indices total


# 5. Constraints

## 5.1. Balance constraints

Tại mỗi mốc thời gian, số tàu đậu đỗ theo từng loại tàu của mỗi mốc thời gian + số tàu bay hạ cánh phải tương đương với số tàu đậu đỗ của mốc thời gian kế tiếp + số tàu bay cất cánh (Node1 + inwards = Node2 + outwards). Ngoài ra, để đảm bảo giả định sản phẩm tần suất các tuần giống nhau, time node cuối cùng trong tuần (23h Chủ Nhật) phải balance với node đầu tiên trong tuần (0h Thứ Hai).

In [16]:
def balance_constraint(model, a,d,h,ac):
    # khung giờ đầu tiên của thứ hai phải cân bằng với khung giờ cuối cùng của chủ nhật
    # (giả định sản phẩm tần suất của các tuần giống nhau)
    if h == 0 and d == 1:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,7,23,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == 7)
                    &(data['ETA'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == 7)
                    &(data['ETD'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    # khung giờ đầu tiên trong ngày = khung giờ cuối cùng ngày hôm trước:
    elif h == 0:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,d-1,23,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == d-1)
                    &(data['ETA'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == d-1)
                    &(data['ETD'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    # balance constraint cho các khung giờ trong 1 ngày:
    else:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,d,h-1,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == d)
                    &(data['ETA'].between(h-1,h,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == d)
                    &(data['ETD'].between(h-1,h,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    return expr

In [17]:
model.balance_constraint = pyo.Constraint(airport, DOW, hour, ac_type, rule = balance_constraint)

           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
      169.28 seconds to construct Constraint balance_constraint; 52920 indices total


## 5.2. Coverage constraints

Mỗi 1 số hiệu chuyến bay nếu được lựa chọn khai thác thì chỉ được dùng duy nhất 1 loại tàu bay trong ngày. (Vd: VN087 không thể khai thác đồng thời 321 và 787 tại cùng 1 ngày).

In [18]:
def coverage_constraint(model, f,d):
    if data[(data['flight']==f)&(data['DOW_ETD']==d)].empty:
        expr = pyo.Constraint.Skip
    else:
        expr = sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['DOW_ETD']==d)]['index']) <= 1
    return expr
# Rieeng các đường xuyên Đông Dương thì sẽ có 2 chuyến bay có chung 1 số hiệu chuyến bay trong 1 ngày, vì vậy phải thêm elif

In [19]:
model.coverage_constraint = pyo.Constraint(flight_no, DOW, rule = coverage_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
        4.70 seconds to construct Constraint coverage_constraint; 3367 indices total


## 5.3. Fleet constraints

Tổng số tàu bay tại các sân bay trong từng khung giờ không được lớn hơn số tàu bay đã thuê mua.

In [20]:
def fleet_constraint(model, d,h,ac):
    return pyo.inequality(0,sum(time_nodes[a,d,h,ac] for a in airport),fleet[ac])
# có thể tính chi phí tàu bay cố định = sum(time_nodes[a,d,h,ac] for a in airport)*chi phí 1 tàu

In [21]:
model.fleet_constraint = pyo.Constraint(DOW, hour, ac_type, rule = fleet_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
        0.13 seconds to construct Constraint fleet_constraint; 840 indices total


## 5.4. Airport constraints

Một số đường bay chỉ dùng được tàu thân rộng, một số đường bay khác chỉ dùng được tàu AT7 do hạn chế về khoảng cách bay và cơ sở hạ tầng sân bay.

In [22]:
long_haul = ['CDG','DME','SVO','FRA','LHR','LAX','SFO','SYD','MEL']

In [23]:
def airport_constraint(model, i):
    return sum(assign_fleet[i] for i in data[(data['AC']=='A321')&(data['to'].isin(long_haul))]['index']) == 0

## 5.5. Product constraints

Để đảm bảo tính đồng nhất của sản phẩm, các chuyến bay trên 1 đường bay phải sử dụng loại tàu bay giống nhau giữa các ngày trong tuần.

In [24]:
def product_constraint(model,f,ac,d):
    operating_day = list(data[(data['flight']==f)&(data['AC']==ac)]['DOW_ETD'])
    if d not in operating_day:
        expr = pyo.Constraint.Skip
    elif d == operating_day[0]:
        expr = pyo.Constraint.Skip
    else:
        expr = (sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['AC']==ac)&(data['DOW_ETD']==d)]['index'])
                == sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['AC']==ac)&(data['DOW_ETD']==operating_day[operating_day.index(d)-1])]['index']))
    return expr

In [25]:
model.product_constraint = pyo.Constraint(flight_no, ac_type, DOW, rule = product_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
       36.08 seconds to construct Constraint product_constraint; 16835 indices total


Một số đường bay bắt buộc phải khai thác:

In [26]:
for i in data[(data['ROUTE']=='SGNCDG')&(data['AC']=='A350')]['index']:
    assign_fleet[i].fix(1)

# 6. Objective function

In [27]:
model.obj = pyo.Objective(expr = (sum(assign_fleet[i]*data[data['index']==i]['revenue'].values[0] for i in flight_index)
                          -sum(assign_fleet[i]*data[data['index']==i]['cost'].values[0] for i in flight_index)), sense = pyo.maximize)

           0 seconds to construct Objective obj; 1 index total


In [28]:
solver = SolverFactory('cbc', executable = "C:\\Users\\namtrantuan\\Desktop\\FAM\\coin\\cbc.exe")

In [29]:
results = solver.solve(model, tee=True)

Welcome to the CBC MILP Solver 
Version: 2.10.5 
Build Date: Nov 24 2021 

command line - C:\Users\namtrantuan\Desktop\FAM\coin\cbc.exe -printingOptions all -import C:\Users\NAMTRA~1\AppData\Local\Temp\tmp6tusv1pr.pyomo.lp -stat=1 -solve -solu C:\Users\NAMTRA~1\AppData\Local\Temp\tmp6tusv1pr.pyomo.soln (default strategy 1)
Option for printingOptions changed from normal to all
 CoinLpIO::readLp(): Maximization problem reformulated as minimization
Coin0009I Switching back to maximization to get correct duals etc
Presolve is modifying 1 integer bounds and re-presolving
Presolve 4610 (-59021) rows, 4976 (-55811) columns and 49411 (-198759) elements
Statistics for presolved model
Original problem has 60785 integers (7865 of which binary)
Presolved problem has 4976 integers (1458 of which binary)
==== 3518 zero objective 270 different
==== absolute objective values 270 different
==== for integers 3518 zero objective 270 different
==== for integers absolute objective values 270 different
====

Cbc0010I After 6600 nodes, 1812 on tree, -105546.81 best solution, best possible -105627.84 (1227.18 seconds)
Cbc0010I After 6700 nodes, 1861 on tree, -105546.81 best solution, best possible -105627.84 (1241.92 seconds)
Cbc0010I After 6800 nodes, 1910 on tree, -105546.81 best solution, best possible -105627.84 (1258.62 seconds)
Cbc0010I After 6900 nodes, 1962 on tree, -105546.81 best solution, best possible -105627.84 (1273.22 seconds)
Cbc0010I After 7000 nodes, 2009 on tree, -105546.81 best solution, best possible -105627.84 (1289.66 seconds)
Cbc0010I After 7100 nodes, 2060 on tree, -105546.81 best solution, best possible -105627.84 (1304.83 seconds)
Cbc0038I Full problem 4603 rows 4975 columns, reduced to 1253 rows 814 columns
Cbc0010I After 7200 nodes, 2109 on tree, -105546.81 best solution, best possible -105627.84 (1317.85 seconds)
Cbc0010I After 7300 nodes, 2160 on tree, -105546.81 best solution, best possible -105627.84 (1333.03 seconds)
Cbc0010I After 7400 nodes, 2209 on tree, 

Cbc0010I After 17200 nodes, 2572 on tree, -105615.52 best solution, best possible -105620.98 (2513.68 seconds)
Cbc0010I After 17300 nodes, 2552 on tree, -105615.52 best solution, best possible -105620.98 (2519.28 seconds)
Cbc0010I After 17400 nodes, 2541 on tree, -105615.52 best solution, best possible -105620.98 (2525.87 seconds)
Cbc0010I After 17500 nodes, 2528 on tree, -105615.52 best solution, best possible -105620.98 (2531.67 seconds)
Cbc0010I After 17600 nodes, 2518 on tree, -105615.52 best solution, best possible -105620.98 (2538.01 seconds)
Cbc0010I After 17700 nodes, 2492 on tree, -105615.52 best solution, best possible -105620.98 (2544.45 seconds)
Cbc0010I After 17800 nodes, 2482 on tree, -105615.52 best solution, best possible -105620.98 (2550.92 seconds)
Cbc0010I After 17900 nodes, 2469 on tree, -105615.52 best solution, best possible -105620.98 (2557.41 seconds)
Cbc0010I After 18000 nodes, 2458 on tree, -105615.52 best solution, best possible -105620.98 (2563.61 seconds)
C

Cbc0010I After 28200 nodes, 2408 on tree, -105615.52 best solution, best possible -105619.91 (3311.87 seconds)
Cbc0010I After 28300 nodes, 2393 on tree, -105615.52 best solution, best possible -105619.89 (3318.70 seconds)
Cbc0010I After 28400 nodes, 2387 on tree, -105615.52 best solution, best possible -105619.87 (3325.97 seconds)
Cbc0010I After 28500 nodes, 2372 on tree, -105615.52 best solution, best possible -105619.84 (3333.01 seconds)
Cbc0010I After 28600 nodes, 2362 on tree, -105615.52 best solution, best possible -105619.81 (3339.80 seconds)
Cbc0010I After 28700 nodes, 2346 on tree, -105615.52 best solution, best possible -105619.79 (3347.04 seconds)
Cbc0010I After 28800 nodes, 2329 on tree, -105615.52 best solution, best possible -105619.76 (3354.32 seconds)
Cbc0010I After 28900 nodes, 2312 on tree, -105615.52 best solution, best possible -105619.73 (3361.28 seconds)
Cbc0010I After 29000 nodes, 2298 on tree, -105615.52 best solution, best possible -105619.7 (3368.18 seconds)
Cb

Cbc0010I After 39200 nodes, 141 on tree, -105615.52 best solution, best possible -105615.53 (3971.09 seconds)
Cbc0010I After 39300 nodes, 136 on tree, -105615.52 best solution, best possible -105615.53 (3977.67 seconds)
Cbc0010I After 39400 nodes, 136 on tree, -105615.52 best solution, best possible -105615.53 (3984.70 seconds)
Cbc0010I After 39500 nodes, 134 on tree, -105615.52 best solution, best possible -105615.53 (3992.68 seconds)
Cbc0010I After 39600 nodes, 124 on tree, -105615.52 best solution, best possible -105615.53 (4000.28 seconds)
Cbc0038I Full problem 4603 rows 4975 columns, reduced to 781 rows 430 columns
Cbc0010I After 39700 nodes, 120 on tree, -105615.52 best solution, best possible -105615.53 (4007.28 seconds)
Cbc0010I After 39800 nodes, 121 on tree, -105615.52 best solution, best possible -105615.53 (4013.91 seconds)
Cbc0010I After 39900 nodes, 124 on tree, -105615.52 best solution, best possible -105615.53 (4021.20 seconds)
Cbc0010I After 40000 nodes, 120 on tree, -


Objective value:                105615.52388877
Enumerated nodes:               45431
Total iterations:               10245251
Time (CPU seconds):             4345.40
Time (Wallclock seconds):       4345.30

Total time (CPU seconds):       4346.68   (Wallclock seconds):       4346.59



# 7. Results

In [30]:
model.pprint()

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



        Key               : Lower : Value : Upper : Fixed : Stale : Domain
         BKKHANVN610787A1 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A2 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A3 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A4 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A5 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A6 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787A7 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B1 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B2 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B3 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B4 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B5 :     0 :   0.0 :     1 : False : False : Binary
         BKKHANVN610787B6

        DLISGNVN1381A3216 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1381A3217 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3211 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3212 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3213 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3214 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3215 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3216 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1383A3217 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1385A3215 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN1385A3217 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN7381A3211 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN7381A3212 :     0 :   1.0 :     1 : False : False : Binary
        DLISGNVN7381A3213

        HANVCAVN1207A3211 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3212 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3213 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3214 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3215 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3216 :     0 :   0.0 :     1 : False : False : Binary
        HANVCAVN1207A3217 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3211 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3212 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3213 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3214 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3215 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3216 :     0 :   0.0 :     1 : False : False : Binary
        HANVCLVN1641A3217

         SGNHANVN252787A7 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252787B3 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252787B5 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252787B7 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252787C3 :     0 :   1.0 :     1 : False : False : Binary
         SGNHANVN252787C5 :     0 :   1.0 :     1 : False : False : Binary
         SGNHANVN252787C7 :     0 :   1.0 :     1 : False : False : Binary
         SGNHANVN252A3213 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252A3215 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252A3217 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252A3503 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252A3505 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN252A3507 :     0 :   0.0 :     1 : False : False : Binary
         SGNHANVN256787A1

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



        Key           : Lower : Body                                                                                                                                                                    : Upper : Active
          ('VN10', 3) :  -Inf :                                           assign_fleet[CDGSGNVN10A3503] + assign_fleet[CDGSGNVN10787A3] + assign_fleet[CDGSGNVN10787B3] + assign_fleet[CDGSGNVN10787C3] :   1.0 :   True
          ('VN10', 5) :  -Inf :                                           assign_fleet[CDGSGNVN10A3505] + assign_fleet[CDGSGNVN10787A5] + assign_fleet[CDGSGNVN10787B5] + assign_fleet[CDGSGNVN10787C5] :   1.0 :   True
          ('VN10', 7) :  -Inf :                                           assign_fleet[CDGSGNVN10A3507] + assign_fleet[CDGSGNVN10787A7] + assign_fleet[CDGSGNVN10787B7] + assign_fleet[CDGSGNVN10787C7] :   1.0 :   True
         ('VN105', 1) :  -Inf :      assign_fleet[DADSGNVN105A3211] + assign_fleet[DADSGNVN105A3501] + assign_fleet[DADSGNVN105787A1

        ('VN7381', 7) :  -Inf :                                                                                                                                         assign_fleet[DLISGNVN7381A3217] :   1.0 :   True
        ('VN7392', 1) :  -Inf :                                                                                                                                         assign_fleet[SGNUIHVN7392A3211] :   1.0 :   True
        ('VN7392', 2) :  -Inf :                                                                                                                                         assign_fleet[SGNUIHVN7392A3212] :   1.0 :   True
        ('VN7392', 3) :  -Inf :                                                                                                                                         assign_fleet[SGNUIHVN7392A3213] :   1.0 :   True
        ('VN7392', 4) :  -Inf :                                                                                                     

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




         ('VN513', 'A321', 5) :   0.0 :                                                                                                                                       assign_fleet[PEKHANVN513A3215] - assign_fleet[PEKHANVN513A3213] :   0.0 :   True
         ('VN513', 'A321', 6) :   0.0 :                                                                                                                                       assign_fleet[PEKHANVN513A3216] - assign_fleet[PEKHANVN513A3215] :   0.0 :   True
         ('VN513', 'A321', 7) :   0.0 :                                                                                                                                       assign_fleet[PEKHANVN513A3217] - assign_fleet[PEKHANVN513A3216] :   0.0 :   True
         ('VN513', 'A350', 3) :   0.0 :                                                                                                                                       assign_fleet[PEKHANVN513A3503] - assign_fleet[PEKHANVN513A35

In [31]:
results.solver.status

<SolverStatus.ok: 'ok'>

In [32]:
results.solver.termination_condition

<TerminationCondition.optimal: 'optimal'>

In [33]:
optimal_values = [value(assign_fleet[i]) for i in assign_fleet]

In [34]:
df_time_nodes = pd.DataFrame.from_dict(time_nodes.extract_values(), orient="index", columns=["variable value"])
df_time_nodes.reset_index(inplace = True)
print(df_time_nodes)

                    index  variable value
0       (VDH, 1, 0, A321)             0.0
1       (VDH, 1, 0, A350)             0.0
2       (VDH, 1, 0, 787A)             0.0
3       (VDH, 1, 0, 787B)             0.0
4       (VDH, 1, 0, 787C)             0.0
...                   ...             ...
52915  (LHR, 7, 23, A321)             0.0
52916  (LHR, 7, 23, A350)             0.0
52917  (LHR, 7, 23, 787A)             0.0
52918  (LHR, 7, 23, 787B)             0.0
52919  (LHR, 7, 23, 787C)             0.0

[52920 rows x 2 columns]


In [35]:
df_time_nodes.to_excel('time_nodes.xlsx')

In [36]:
df_assign_fleet = pd.DataFrame.from_dict(assign_fleet.extract_values(), orient='index', columns=[str(assign_fleet)])
df_assign_fleet.reset_index(inplace = True)
print(df_assign_fleet)

                 index  assign_fleet
0     DADHANVN154A3211           0.0
1     DADHANVN154A3212           0.0
2     DADHANVN154A3213           0.0
3     DADHANVN154A3214           0.0
4     DADHANVN154A3215           0.0
...                ...           ...
7867  SYDSGNVN772787C3           0.0
7868  SYDSGNVN772787C4           0.0
7869  SYDSGNVN772787C5           0.0
7870  SYDSGNVN772787C6           0.0
7871  SYDSGNVN772787C7           0.0

[7872 rows x 2 columns]


In [37]:
result = data.merge(df_assign_fleet, on = 'index')

In [38]:
result.to_excel('result.xlsx')